# 데이터 수집

## 1. 한국은행 금융통화위원회 의사록


In [2]:
import requests
from bs4 import BeautifulSoup as bs
from urllib.request import urlretrieve
import urllib.request
import pandas as pd
import pdfplumber
import re
import os
import shutil

In [12]:
def get_mpb_minutes(start_date = '2008-04-01', end_date = '2022-11-15'):
    
    url = 'https://www.bok.or.kr/portal/bbs/B0000245/list.do?menuNo=200761&searchWrd=&searchCnd=1' 
    headers = {'user-agent' : 'Mozilla/5.0'}
    page = 1
    texts = []

    while True:
        params = f'&sdate={start_date}&edate={end_date}&pageIndex={str(page)}'
        resp = requests.get(url + params, headers = headers)
        soup = bs(resp.text, 'lxml')
        end_page = soup.select('.schTotal span')[-1].text.split('/')[1].replace('pages', '')
        
        if page <= int(end_page):
            print(f'{page}번째 페이지 크롤링')
            aTag_list = soup.select('.fileGoupBox a')
            href_list = [aTag.attrs['href'] for aTag in aTag_list if '.pdf' in aTag.attrs['title']] 
            for href in href_list:
                print(href)
                download_link = 'https://www.bok.or.kr' + href
                os.makedirs('/content/temp')
                urlretrieve(download_link, '/content/temp/temp.pdf')

                text = ""
                with pdfplumber.open('/content/temp/temp.pdf') as f:
                    pages = f.pages      
                    for pg in pages[1:]:
                        text += pg.extract_text().replace('\n', '')
                        text = re.sub('- \d+ -', '', text)
                shutil.rmtree('/content/temp')
                texts.append(text)
            page += 1
        else: break

    return texts

In [13]:
text = get_mpb_minutes()

1번째 페이지 크롤링
/portal/cmmn/file/fileDown.do?menuNo=200761&atchFileId=FILE_000000000035091&fileSn=2
/portal/cmmn/file/fileDown.do?menuNo=200761&atchFileId=FILE_000000000034867&fileSn=2
/portal/cmmn/file/fileDown.do?menuNo=200761&atchFileId=FILE_000000000034406&fileSn=2
/portal/cmmn/file/fileDown.do?menuNo=200761&atchFileId=FILE_000000000034210&fileSn=2
/portal/cmmn/file/fileDown.do?menuNo=200761&atchFileId=FILE_000000000034051&fileSn=2
/portal/cmmn/file/fileDown.do?menuNo=200761&atchFileId=FILE_000000000033255&fileSn=2
/portal/cmmn/file/fileDown.do?menuNo=200761&atchFileId=FILE_000000000033019&fileSn=2
/portal/cmmn/file/fileDown.do?menuNo=200761&atchFileId=FILE_000000000032246&fileSn=2
/portal/cmmn/file/fileDown.do?menuNo=200761&atchFileId=FILE_000000000031946&fileSn=2
/portal/cmmn/file/fileDown.do?menuNo=200761&atchFileId=FILE_000000000031705&fileSn=2
2번째 페이지 크롤링
/portal/cmmn/file/fileDown.do?menuNo=200761&atchFileId=FILE_000000000030802&fileSn=2
/portal/cmmn/file/fileDown.do?menuNo=2007

In [15]:
with open('/content/mpb_minutes.txt', 'w') as f:
    for text in texts:
        f.write(text + '\n')

In [16]:
# #데이터 불러오기
# minutes_df = pd.read_csv('mpb_minutes.txt', sep='\t', header=None).transpose()
# minutes_df.drop(index=300, axis=0, inplace=True)
# minutes_df.columns = ['docs']
# minutes_df

doc
0    1. 일 자 2022년 10월 27일(목)2. 장 소 금융통화위원회 회의실3. 출석...
1    1. 일 자 2022년 10월 12일(수)2. 장 소 금융통화위원회 회의실3. 출석...
2    1. 일 자 2022년 9월 22일(목)2. 장 소 금융통화위원회 회의실3. 출석위...
3    1. 일 자 2022년 9월 8일(목)2. 장 소 금융통화위원회 회의실3. 출석위원...
4    1. 일 자 2022년 8월 25일(목)2. 장 소 금융통화위원회 회의실3. 출석위...
..                                                 ...
295  동향 국제국장이 보고 제 호 외환국제금융 동향 그리고 금융시장국장이, 52 - ,보...
296  본회의에서는 의장이 한국은행법 제 조에 의거하여 의안 제 호 통( ) 28 21 -...
297  년도 연차보고서 안 은 공개시장조작 및 고액권 발행 준비 등 주2007 ( )요 업...
298  전일 개최된 동향보고회의에서 조사국장이 보고 제 호 국내외 경제( ) 26 -동향 ...
299  전일 개최된 동향보고회의에서 조사국장이 보고 제 호 국내외 경제( ) 16 -동향 ...

[300 rows x 1 columns]

In [17]:
# minutes_df.to_csv('minutes_df.csv')

In [1]:
# #데이터 불러오기
# with open('mpb_minutes.txt', 'r', encoding= 'utf-8') as f:
#      minutes = f.read()
    
# minutes

"1. 일 자 2022년 10월 27일(목)2. 장 소 금융통화위원회 회의실3. 출석위원 이 창 용 의 장(총재)조 윤 제 위 원서 영 경 위 원주 상 영 위 원이 승 헌 위 원(부총재)박 기 영 위 원신 성 환 위 원4. 결석위원 없 음5. 참 여 자 강 승 준 감사 이 환 석 부총재보배 준 석 부총재보 민 좌 홍 부총재보이 상 형 부총재보 이 종 렬 부총재보양 석 준 외자운용원장 김 웅 조사국장이 정 욱 금융안정국장 홍 경 식 통화정책국장김 인 구 금융시장국장 이 한 녕 금융결제국장오 금 화 국제국장 박 양 수 경제연구원장김 용 식 공보관 한 승 철 금융통화위원회실장최 문 성 의사팀장6. 회의경과가. 의결안건<의안 제36호 – ｢한국은행의 금융기관대출규정｣ 개정(안)>(１) 담당 부총재보가「한국은행법」제28조제3호 및 제68조에 의거 한국은행이금융기관에 대한 대출의 담보로 취득할 수 있는 증권의 범위를 한시적으로 확대하고자 한다는 내용의 제안설명을 하였음.(２) 위원 토의내용제안설명에 이어 관련부서에서는 위원협의회에서 논의된 주요내용을 다음과같이 보고하였음.여러 위원들은 대출 적격담보증권의 범위 확대와 관련하여 동 조치가 가지는개별적 의미보다는 통화정책 기조 전반에 대한 함의를 진솔하게 논의할 필요가있으며, 이 같은 정책 시행의 배경과 효과 등에 주목해야 한다는 의견을 나타내었음.이에 대해 관련부서에서는 최근 시장 유동성 사정이 다소 위축된 근저에 담보 이슈가 있다고 판단하고 있으며, 동 조치가 이 같은 이슈 해결에 도움이 되어금융시장을 단기적으로 안정화시키는 효과가 있을 것으로 보고 있다고 답변하였음. 아울러 이로 인해 물가 중심의 통화정책 기조를 이어갈 수 있는 여건이 저해되지 않도록 하는 측면도 있다고 덧붙였음.일부 위원은 긴축적인 통화정책은 필연적으로 시장에 어느 정도의 충격을 유발하게 되는데 그때마다 대책을 시행하는 것이 적절한지에 대해 근본적인 고민이필요하다고 언급하면서, 앞으로 일정 기간 고금리 상태가 지속될 수 있는데 그과정에서 발생할 수 있